In [ ]:
"""
This notebook allows custom match functions to be used to define match criteria for comparing scenarios between the 
control and candidate branches. One-to-many matches are allowed.
"""
from mined_metric.jupyter.utils.data_access_util import get_experiment_data, get_validation_data
from mined_metric.jupyter.utils.data_processing_util import get_unique_id
from mined_metric.jupyter.utils.validation_vis_util import create_match_matrix, vis_one_to_many_metrics_diff

In [ ]:
EXP_ID_CONTROL = "EXP_ID_CONTROL_PLACEHOLDER"
EXP_ID_CANDIDATE = "EXP_ID_CANDIDATE_PLACEHOLDER"
VALIDATION_ID = "VALIDATION_ID_PLACEHOLDER"

if "PLACEHOLDER" not in VALIDATION_ID:
    exp_data_control, exp_data_candidate = get_validation_data(VALIDATION_ID)
else:
    exp_data_control = get_experiment_data(EXP_ID_CONTROL)
    exp_data_candidate = get_experiment_data(EXP_ID_CANDIDATE)

meta_data_control = exp_data_control["meta"]
meta_data_candidate = exp_data_candidate["meta"]

In [ ]:
# User defined match function
def match_function(scenario_1, scenario_2):
    """ Match condition: the chum URIs' start times are within 10 seconds of each other """
    if "sim_failed" in scenario_1 or "sim_failed" in scenario_2:
        return False

    max_time_diff_s = 1000
    uri_1 = get_unique_id(scenario_1["chum_uri"])
    uri_2 = get_unique_id(scenario_2["chum_uri"])
    vehicle_1 = uri_1.split("@")[0].split("-")[-1]
    vehicle_2 = uri_2.split("@")[0].split("-")[-1]
    start_1 = int(uri_1.split("@")[1].split("-")[0].split(".")[0])
    start_2 = int(uri_2.split("@")[1].split("-")[0].split(".")[0])

    return (vehicle_1 == vehicle_2 and
            abs(start_1 - start_2) < max_time_diff_s)

In [ ]:
# Import Qgrid for visualizing the comparison table
import sys
!{sys.executable} -m pip install qgrid
!sudo jupyter nbextension enable --py --sys-prefix qgrid
!sudo jupyter nbextension enable --py --sys-prefix widgetsnbextension
sys.path.append("/home/zoox/.local/lib/python3.6/site-packages")
import qgrid

In [ ]:
# If nothing shows up after running this cell, run the cell above and restart the server
match_matrix = create_match_matrix(meta_data_control, meta_data_candidate, match_function)
df = vis_one_to_many_metrics_diff(match_matrix, meta_data_control, meta_data_candidate)
grid_options = {
    "forceFitColumns": False,
}
qgrid_widget = qgrid.show_grid(df, grid_options=grid_options)
qgrid_widget